<a href="https://colab.research.google.com/github/AvantiShri/oceanography_colab_notebooks/blob/master/for_rian/V1_Pacific_Ocean_GLODAP_ArchetypeAnalysis_WaterMasses.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install py_pcha
!pip install gsw

     |████████████████████████████████| 2.4MB 2.8MB/s 


Grab the data

In [2]:
#!wget --no-check-certificate 'https://docs.google.com/uc?export=download&id=1E9XGag2_uC2TM_5DcOcmSz86I1xj6hHr' -O GLODAPv2.2019_Pacific_Ocean.csv
#For large files, this is the command:
!wget --load-cookies /tmp/cookies.txt "https://docs.google.com/uc?export=download&confirm=$(wget --quiet --save-cookies /tmp/cookies.txt --keep-session-cookies --no-check-certificate 'https://docs.google.com/uc?export=download&id=1E9XGag2_uC2TM_5DcOcmSz86I1xj6hHr' -O- | sed -rn 's/.*confirm=([0-9A-Za-z_]+).*/\1\n/p')&id=1E9XGag2_uC2TM_5DcOcmSz86I1xj6hHr" -O GLODAPv2.2019_Pacific_Ocean.csv && rm -rf /tmp/cookies.txt

--2020-08-31 09:50:42--  https://docs.google.com/uc?export=download&confirm=XbKl&id=1E9XGag2_uC2TM_5DcOcmSz86I1xj6hHr
Resolving docs.google.com (docs.google.com)... 74.125.204.138, 74.125.204.102, 74.125.204.113, ...
Connecting to docs.google.com (docs.google.com)|74.125.204.138|:443... connected.
HTTP request sent, awaiting response... 302 Moved Temporarily
Location: https://doc-00-78-docs.googleusercontent.com/docs/securesc/61bqrh59lk6es7m7csok6i6rrbec6ams/euo67p13n246ntdmd12im5l35nbn30r4/1598867400000/06203730782251856755/04984333340609291722Z/1E9XGag2_uC2TM_5DcOcmSz86I1xj6hHr?e=download [following]
--2020-08-31 09:50:43--  https://doc-00-78-docs.googleusercontent.com/docs/securesc/61bqrh59lk6es7m7csok6i6rrbec6ams/euo67p13n246ntdmd12im5l35nbn30r4/1598867400000/06203730782251856755/04984333340609291722Z/1E9XGag2_uC2TM_5DcOcmSz86I1xj6hHr?e=download
Resolving doc-00-78-docs.googleusercontent.com (doc-00-78-docs.googleusercontent.com)... 64.233.189.132, 2404:6800:4008:c07::84
Connecting

In [3]:
from matplotlib import pyplot as plt
import numpy as np
import pandas
import gsw

In [6]:
list(df.columns)

['cruise',
 'station',
 'cast',
 'year',
 'month',
 'day',
 'hour',
 'minute',
 'latitude',
 'longitude',
 'bottomdepth',
 'maxsampdepth',
 'bottle',
 'pressure',
 'depth',
 'temperature',
 'theta',
 'salinity',
 'salinityf',
 'salinityqc',
 'sigma0',
 'sigma1',
 'sigma2',
 'sigma3',
 'sigma4',
 'gamma',
 'oxygen',
 'oxygenf',
 'oxygenqc',
 'aou',
 'aouf',
 'nitrate',
 'nitratef',
 'nitrateqc',
 'nitrite',
 'nitritef',
 'silicate',
 'silicatef',
 'silicateqc',
 'phosphate',
 'phosphatef',
 'phosphateqc',
 'tco2',
 'tco2f',
 'tco2qc',
 'talk',
 'talkf',
 'talkqc',
 'phts25p0',
 'phts25p0f',
 'phtsinsitutp',
 'phtsinsitutpf',
 'phtsqc',
 'cfc11',
 'pcfc11',
 'cfc11f',
 'cfc11qc',
 'cfc12',
 'pcfc12',
 'cfc12f',
 'cfc12qc',
 'cfc113',
 'pcfc113',
 'cfc113f',
 'cfc113qc',
 'ccl4',
 'pccl4',
 'ccl4f',
 'ccl4qc',
 'sf6',
 'psf6',
 'sf6f',
 'c13',
 'c13f',
 'c13qc',
 'c14',
 'c14f',
 'c14err',
 'h3',
 'h3f',
 'h3err',
 'he3',
 'he3f',
 'he3err',
 'he',
 'hef',
 'heerr',
 'neon',
 'neonf',
 'n

Read in the data frame and rename the columns

In [12]:
#Easy remapping of the column names
colnames_map = {'latitude':"latitude",
            'longitude':"longitude",
            'year':"year",
            'depth (m)':"depth",
            'pressure (dbar)':"pressure",
            'temperature(degrees C)':"temperature",
            'salinity (psu)':"salinity",
            'oxygen (umol/kg)':"oxygen",
            'silicate (umol/kg)':"silicate",
            'nitrate (umol/kg)':"nitrate",
            'phosphate (umol/kg)':"phosphate",
            'potential density':"sigma0",
            }

ROUNDING_PRECISION = 4


#For some reason, altair chokes when provided data frames with some
# of the original column names. So I am remapping the column names.
def remap_colnames(df, colnames_map):
  remapnames_df = pandas.DataFrame(dict([
      (new_col, np.array(df[orig_col]))
      for new_col,orig_col in colnames_map.items()]))
  return remapnames_df

df = pandas.read_csv("GLODAPv2.2019_Pacific_Ocean.csv", na_values = -9999)
df.columns
#, sep='delimiter',header=None
remapnames_df = remap_colnames(df=df, colnames_map=colnames_map)
#create a column for calculated variables
remapnames_df['NO'] = remapnames_df['oxygen (umol/kg)'] + (remapnames_df['nitrate (umol/kg)']*9.68)
remapnames_df['PO'] = remapnames_df['oxygen (umol/kg)'] + (remapnames_df['phosphate (umol/kg)']*155)
remapnames_df['pt'] = np.round(
    gsw.pt_from_t(remapnames_df['salinity (psu)'],
                  remapnames_df['temperature(degrees C)'],
                  remapnames_df['pressure (dbar)'],
                  remapnames_df['potential density']),
   decimals=ROUNDING_PRECISION)


Prepare the features that define the convex hull

In [31]:
import sklearn.impute
import time

#the columns to use for defining the convex hull
COLUMNS_TO_COMPARE = [
            'pt',
            'salinity (psu)',
            'silicate (umol/kg)',
            'potential density',
            'PO',
            'NO']

print("Standardizing feature values")
#Let's standardize each column by subtracting mean and
# dividing by standard deviation. Call it a 'features' dataframe
features_df = pandas.DataFrame()
#keep track of mean and std in order to do inverse transform
colname_to_mean = {}
colname_to_std = {} 
for colname in COLUMNS_TO_COMPARE:
  vals = np.array(remapnames_df[colname])
  #use nanmean and nanstd to ignore nan values for now
  mean = np.nanmean(vals)
  std = np.nanstd(vals)
  colname_to_mean[colname] = mean
  colname_to_std[colname] = std
  features_df['zscore_'+colname] = (vals-mean)/std

#Since imputation takes a while on such a large dataset, we
# will just drop rows that have missing values
print("Proportions of missing values:")
print(np.sum(np.isnan(features_df)) / len(features_df))
print("Original number of rows:", len(features_df))
features_df = features_df.dropna()
print("Remaining rows after dropping missing vals:",len(features_df))
dropna_remapnames_df = remapnames_df.dropna()
assert len(dropna_remapnames_df) == len(features_df)

#print("Running KNN imputation")
#start = time.time()
##we impute nan values using KNNImputer
#features_df = pandas.DataFrame(data=sklearn.impute.KNNImputer(
#    missing_values=np.nan, n_neighbors=5,
#    weights='distance').fit_transform(features_df),
#    columns=features_df.columns)
#print("KNN imputation took", time.time()-start)

#prepare a 'features' matrix for each point
features = np.array([np.array(features_df["zscore_"+col])
                     for col in COLUMNS_TO_COMPARE]).transpose((1,0))

TRANSFORM_MEANS = np.array([colname_to_mean[colname]
                           for colname in COLUMNS_TO_COMPARE])
TRANSFORM_STDS = np.array([colname_to_std[colname]
                           for colname in COLUMNS_TO_COMPARE])
#map features back to original space
def map_features_back(features):
  return features*TRANSFORM_STDS[None,:] + TRANSFORM_MEANS[None,:]

Standardizing feature values
Proportions of missing values:
zscore_pt                    0.013672
zscore_salinity (psu)        0.011072
zscore_silicate (umol/kg)    0.198236
zscore_potential density     0.013564
zscore_PO                    0.196824
zscore_NO                    0.183883
dtype: float64
Original number of rows: 452744
Remaining rows after dropping missing vals: 339929


In [32]:
#Defining some helper functions for storing the archetype info and making
# altair-friendly dataframes

from collections import OrderedDict


#save the reconstructed features in the original feature space
def save_reconstructed_features(reconstructed_features, df):
  #map features back to the original space
  reconstructed_orig_features = map_features_back(reconstructed_features)
  for feature_idx, colname in enumerate(COLUMNS_TO_COMPARE):
    df["reconstructed_"+colname] = np.round(
        reconstructed_orig_features[:,feature_idx], decimals=ROUNDING_PRECISION)


#Create a df where there is a feature called 'composition' and a feature
# called 'archetype', and 'composition' indicates the proportion of the
# archetype
def get_archetype_composition_df(orig_df):
  feature_names = list(remapnames_df.columns)
  df_dict = OrderedDict()

  #initialize feature_dict
  for feature_name in feature_names:
    df_dict[feature_name] = []
  df_dict["archetype"] = []
  df_dict["composition"] = []

  for archetype_num in range(NUM_ENDMEMBERS):
    archetype_str = getarchetypename(archetype_num)
    archetype_fraction = orig_df[archetype_str]
    for feature_name in feature_names:
      df_dict[feature_name].extend(list(orig_df[feature_name]))
    df_dict["composition"].extend(list(orig_df[archetype_str]))
    df_dict["archetype"].extend([archetype_str for i in range(len(orig_df))])

  return pandas.DataFrame(df_dict)

In [38]:
#Let's identify archetypes
from py_pcha import PCHA
import matplotlib

numendmembers_to_archetyperesult = {}

for num_endmembers in [2,3,4,5,6,7,8]:
  print("Running archetype analysis with",num_endmembers,"archetypes")
  XC, S, C, SSE, varexpl = PCHA(X=features.T, noc=num_endmembers, verbose=True)
  print(str(num_endmembers)+" archetypes; variance explained:", varexpl)
  numendmembers_to_archetyperesult[num_endmembers] = (XC, S, C, SSE, varexpl)



Streaming output truncated to the last 5000 lines.
        62 |     0.8915 | 2.1246e+05 | 2.0225e-03 | 5.1660e-04 | 1.0000e+00 | 1.5400e-03 |     1.0000 

        63 |     0.8917 | 2.1200e+05 | 2.1443e-03 | 4.9979e-05 | 1.0000e+00 | 2.3839e-03 |     1.0000 

        64 |     0.8919 | 2.1163e+05 | 1.7584e-03 | 3.0946e-04 | 1.0000e+00 | 1.8451e-03 |     1.0000 

        65 |     0.8922 | 2.1116e+05 | 2.2451e-03 | 5.9877e-05 | 1.0000e+00 | 2.8560e-03 |     1.0000 

        66 |     0.8924 | 2.1076e+05 | 1.8616e-03 | 3.7074e-04 | 1.0000e+00 | 2.2105e-03 |     1.0000 

        67 |     0.8926 | 2.1030e+05 | 2.2004e-03 | 2.8694e-04 | 1.0000e+00 | 1.7108e-03 |     1.0000 

        68 |     0.8929 | 2.0967e+05 | 3.0151e-03 | 1.7767e-03 | 1.0000e+00 | 2.6483e-03 |     1.0000 

        69 |     0.8931 | 2.0921e+05 | 2.1754e-03 | 1.7189e-04 | 1.0000e+00 | 2.0497e-03 |     1.0000 

        70 |     0.8934 | 2.0872e+05 | 2.3605e-03 | 1.0643e-03 | 1.0000e+00 | 1.5864e-03 |     1.0000 

        71 | 

In [60]:
import h5py
#save the results of the archetype analysis at different numbers for total archetypes
archetype_analysis_results = h5py.File("archetype_analysis_results.h5", "w")
for num_endmembers in numendmembers_to_archetyperesult:
  grp = archetype_analysis_results.create_group(str(num_endmembers))
  (XC, S, C, SSE, varexpl) = numendmembers_to_archetyperesult[num_endmembers]
  grp.create_dataset("XC", data=np.array(XC))
  grp.create_dataset("S", data=np.array(S))
  grp.create_dataset("C", data=np.array(C))
  grp.attrs["SSE"] = SSE
  grp.attrs["varexpl"] = varexpl
archetype_analysis_results.close()


In [63]:
h5py.File("archetype_analysis_results.h5", "r")['2'].attrs['varexpl']

0.7313784920780221

In [65]:
!du -hs archetype_analysis_results.h5

182M	archetype_analysis_results.h5


In [84]:
from collections import OrderedDict

def getarchetypename(archetype_num,num_endmembers):
  return str(archetype_num)+"_"+str(num_endmembers)


#save the proportions of each archetype
def save_archetype_compositions(archetype_compositions, num_endmembers, df):
  for archetype_num in range(archetype_compositions.shape[1]):
    df[getarchetypename(archetype_num, num_endmembers)] = np.round(
      archetype_compositions[:, archetype_num],
      decimals=ROUNDING_PRECISION)


#get the archetypes in the original feature space
def get_archetypes_df(numendmembers_to_archetyperesult):

  colname_to_values = OrderedDict()
  for colname in COLUMNS_TO_COMPARE:
    colname_to_values[colname] = []
  colname_to_values["archetype"] = []
  colname_to_values["num_endmembers"] = []

  for num_endmembers in numendmembers_to_archetyperesult:
    archetype_features = np.array(numendmembers_to_archetyperesult[num_endmembers][0]).transpose()
    save_archetype_compositions(
        archetype_compositions=np.array(numendmembers_to_archetyperesult[num_endmembers][1]).transpose(),
        num_endmembers=num_endmembers,
        df=dropna_remapnames_df)

    print(archetype_features.shape)
    #map features back to the original space
    archetype_orig_features = map_features_back(archetype_features)
    for feature_idx, colname in enumerate(COLUMNS_TO_COMPARE):
      colname_to_values[colname].extend(archetype_orig_features[:,feature_idx])
    colname_to_values["archetype"].extend([getarchetypename(i,num_endmembers)
                                   for i in range(archetype_features.shape[0])])
    colname_to_values["num_endmembers"].extend(
        [str(num_endmembers) for i in range(archetype_features.shape[0])])
  return pandas.DataFrame(colname_to_values)

#get the archetype_dataframe containing original archetype features
archetypes_df = get_archetypes_df(numendmembers_to_archetyperesult)

archetypes_df

(2, 6)
(3, 6)
(4, 6)
(5, 6)
(6, 6)
(7, 6)
(8, 6)


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if sys.path[0] == '':


pt  salinity (psu)  ...  archetype  num_endmembers
0   23.425489       34.791582  ...        0_2               2
1    0.646873       34.422828  ...        1_2               2
2   18.405349        5.134425  ...        0_3               3
3    0.598697       34.687984  ...        1_3               3
4   23.453720       35.938593  ...        2_3               3
5   23.903690       35.885427  ...        0_4               4
6   20.564319        0.681945  ...        1_4               4
7    1.332469       34.561792  ...        2_4               4
8    1.454564       34.637278  ...        3_4               4
9    0.660477       34.699087  ...        0_5               5
10  25.044792       36.219731  ...        1_5               5
11  -0.036988       33.770852  ...        2_5               5
12   5.294263       34.242445  ...        3_5               5
13  20.924591        0.778205  ...        4_5               5
14  -0.192495       34.729021  ...        0_6               6
15   2.237729       34.427161  ...        1_6               6
16  26.133597       36.290719  ...        2_6               6
17  20.746800        0.117300  ...        3_6               6
18   5.616167       34.387352  ...        4_6               6
19   2.537830       33.977030  ...        5_6               6
20  20.311255        1.382636  ...        0_7               7
21  27.980144       36.254952  ...        1_7               7
22   7.949035       31.318501  ...        2_7               7
23   0.534666       34.522979  ...        3_7               7
24  14.501519       35.155400  ...        4_7               7
25  20.396511        1.423478  ...        5_7               7
26   1.538811       34.670842  ...        6_7               7
27  16.456434       35.490367  ...        0_8               8
28  -1.178057       34.790142  ...        1_8               8
29  29.237560       36.136689  ...        2_8               8
30   1.312026       34.667653  ...        3_8               8
31   1.072602       34.168726  ...        4_8               8
32   1.328645       34.714504  ...        5_8               8
33  20.329320        1.165122  ...        6_8               8
34   1.306025       34.685027  ...        7_8               8

[35 rows x 8 columns]

In [74]:
#save_reconstructed_features(
#    reconstructed_features=np.array(XC*S).transpose(),
#    df=remapnames_df)

#archetype_composition_df = get_archetype_composition_df(orig_df=remapnames_df)

##Old code for computing a color when there are only 3 archetypes
#remapnames_df['archetypecolors'] = [
#  matplotlib.colors.rgb2hex((a1,a2,a3))
#  for (a1,a2,a3) in zip(archetype_compositions[:,0],
#                        archetype_compositions[:,1],
#                        archetype_compositions[:,2])
#]

View altair interactive visualizations


In [97]:
import altair as alt

OBS_DF = alt.sample(dropna_remapnames_df, n=5000) #data frame for observations
ARCHETYPES_DF = archetypes_df #data frame for archetypes
CHART_WIDTH=400
CHART_HEIGHT=200
FONTSIZE=10

#convenience functions to turn off default altair behaviour of including
# zero in the axis even if no points are at 0
def nozero_xaxis(field_name):
  return alt.X(field_name, scale=alt.Scale(zero=False))

def nozero_yaxis(field_name, domain=None):
  if (domain is None):
    return alt.Y(field_name, scale=alt.Scale(zero=False))
  else:
    return alt.Y(field_name, scale=alt.Scale(zero=False, domain=domain))

interval_selection = alt.selection_interval()

#define the color property that will be shared for the scatterplots/legend
color = alt.condition(interval_selection, alt.value('lightblue'), alt.value('lightgray'))
#color = alt.condition(COMPOSED_SELECTION, 'squared_errors', alt.value('lightgray'))

tooltip_columns = (
    ['latitude', 'longitude', 'depth (m)']
   +[getarchetypename(i,num_endmembers) for num_endmembers in numendmembers_to_archetyperesult for i in range(num_endmembers)]
   +[x for x in COLUMNS_TO_COMPARE])

#base chart for displaying the observed points

obs_basechart = alt.Chart(OBS_DF).mark_point(opacity=0.2).encode(
  color=color,
  tooltip=tooltip_columns
).properties(width=CHART_WIDTH,
             height=CHART_HEIGHT
).add_selection(interval_selection)

#base chart for displaying the archetypes
numendmembers_select = alt.selection_multi(fields=['num_endmembers'])
numendmembers_color = alt.condition(numendmembers_select,
                        alt.Color('num_endmembers:N', legend=None),
                        alt.value('lightgray'))
archetype_basechart = alt.Chart(ARCHETYPES_DF).mark_point(opacity=1, shape='diamond', size=50).encode(
    color=alt.Color("num_endmembers", scale=alt.Scale(scheme="category10"), legend=None) ).properties(
        width=CHART_WIDTH, height=CHART_HEIGHT).transform_filter(numendmembers_select)
numendmembers_legend = alt.Chart(ARCHETYPES_DF).mark_point().encode(
    y=alt.Y('num_endmembers', axis=alt.Axis(orient='right')),
    color=numendmembers_color).add_selection(numendmembers_select)

def create_scatter(xaxis, yaxis):
  return obs_basechart.encode(nozero_xaxis(xaxis), nozero_yaxis(yaxis)) + archetype_basechart.encode(nozero_xaxis(xaxis), nozero_yaxis(yaxis))
  #return archetype_basechart.encode(nozero_xaxis(xaxis), nozero_yaxis(yaxis))


#compose the whole layout
alt.vconcat(

(create_scatter('pt','salinity (psu)')
| create_scatter('salinity (psu)', 'silicate (umol/kg)')
| create_scatter('pt','silicate (umol/kg)')
| numendmembers_legend ),

(create_scatter('pt','NO')
| create_scatter('salinity (psu)', 'NO')
| create_scatter('silicate (umol/kg)','NO')),
 
(create_scatter('pt','PO')
| create_scatter('salinity (psu)', 'PO')
| create_scatter('NO', 'PO')),

(obs_basechart.encode(nozero_xaxis('latitude'),
             nozero_yaxis('depth (m)', domain=(6000, 0))))

).configure_axis(labelFontSize=FONTSIZE,
                 titleFontSize=FONTSIZE)#.properties(padding=0, spacing=0)
# the padding/spacing doesn't propagate to subcharts propertly


alt.VConcatChart(...)

In [95]:
np.min(remapnames_df['salinity (psu)'])

0.1173